In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F

# ----------------------------
# Basic 3x3 Convolution
# ----------------------------
def conv3x3(in_planes, out_planes, stride=1):
    return nn.Conv2d(in_planes, out_planes, kernel_size=3, stride=stride, padding=1, bias=False)

# ----------------------------
# Basic Residual Block
# ----------------------------
class BasicBlock(nn.Module):
    expansion = 1
    def __init__(self, in_planes, planes, stride=1, downsample=None, is_last=False):
        super().__init__()
        self.is_last = is_last
        self.conv1 = conv3x3(in_planes, planes, stride)
        self.bn1 = nn.BatchNorm2d(planes)
        self.relu = nn.ReLU(inplace=True)
        self.conv2 = conv3x3(planes, planes)
        self.bn2 = nn.BatchNorm2d(planes)
        self.downsample = downsample

    def forward(self, x):
        residual = x
        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)
        out = self.conv2(out)
        out = self.bn2(out)

        if self.downsample is not None:
            residual = self.downsample(x)
        out += residual
        preact = out
        out = F.relu(out)

        if self.is_last:
            return out, preact
        else:
            return out

# ----------------------------
# ResNet CIFAR Modular
# ----------------------------
class ResNet(nn.Module):
    def __init__(self, depth, num_filters=[16,16,32,64], block_name='basicblock', num_classes=100):
        super().__init__()
        assert block_name.lower() == 'basicblock', "Currently only BasicBlock supported"
        assert (depth - 2) % 6 == 0, "Depth must be 6n+2 for BasicBlock"
        n = (depth - 2) // 6

        self.in_planes = num_filters[0]
        self.conv1 = conv3x3(3, num_filters[0])
        self.bn1 = nn.BatchNorm2d(num_filters[0])
        self.relu = nn.ReLU(inplace=True)

        # Residual layers
        self.layer1 = self._make_layer(BasicBlock, num_filters[1], n)
        self.layer2 = self._make_layer(BasicBlock, num_filters[2], n, stride=2)
        self.layer3 = self._make_layer(BasicBlock, num_filters[3], n, stride=2)

        self.avgpool = nn.AvgPool2d(8)
        self.fc = nn.Linear(num_filters[3]*BasicBlock.expansion, num_classes)

        # weight init
        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
            elif isinstance(m, nn.BatchNorm2d):
                nn.init.constant_(m.weight, 1)
                nn.init.constant_(m.bias, 0)

    def _make_layer(self, block, planes, blocks, stride=1):
        downsample = None
        if stride != 1 or self.in_planes != planes*block.expansion:
            downsample = nn.Sequential(
                nn.Conv2d(self.in_planes, planes*block.expansion, kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(planes*block.expansion)
            )

        layers = [block(self.in_planes, planes, stride, downsample, is_last=(blocks==1))]
        self.in_planes = planes*block.expansion
        for i in range(1, blocks):
            layers.append(block(self.in_planes, planes, is_last=(i==blocks-1)))
        return nn.Sequential(*layers)

    def forward(self, x, is_feat=False, preact=False):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        f0 = x

        x, f1_pre = self.layer1(x)
        f1 = x
        x, f2_pre = self.layer2(x)
        f2 = x
        x, f3_pre = self.layer3(x)
        f3 = x

        x = self.avgpool(x)
        x = x.view(x.size(0), -1)
        f4 = x
        x = self.fc(x)

        if is_feat:
            return ([f0,f1,f2,f3,f4], x) if not preact else ([f0,f1_pre,f2_pre,f3_pre,f4], x)
        else:
            return x

# ----------------------------
# Architecture builders
# ----------------------------
def resnet20(num_classes=100): return ResNet(20, num_classes=num_classes)
def resnet32(num_classes=100):
    """ResNet32 matching the standard CIFAR ResNet paper structure."""
    # Use num_filters=[32, 32, 64, 128] to match the checkpoint you want to load
    return ResNet(depth=32, num_filters=[32, 64, 128, 256], block_name='basicblock', num_classes=num_classes)

def resnet56(num_classes=100): return ResNet(56, num_classes=num_classes)
def resnet110(num_classes=100): return ResNet(110, num_classes=num_classes)
def resnet32_basic(num_classes=100): return ResNet(32, num_classes=num_classes)

In [2]:
import torch
from torch.utils.data import DataLoader
from torchvision import datasets, transforms

# ---------------------------
# Device
# ---------------------------
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# ---------------------------
# CIFAR-100 test dataset
# ---------------------------
mean = (0.5071, 0.4867, 0.4408)
std  = (0.2675, 0.2565, 0.2761)

test_tf = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize(mean, std)
])

test_ds = datasets.CIFAR100("./data", train=False, transform=test_tf, download=True)
test_loader = DataLoader(test_ds, batch_size=128, shuffle=False, num_workers=2, pin_memory=True)

# ---------------------------
# Model constructors
# ---------------------------
model_dict = {
    # "ResNet20": resnet20,
    # "ResNet32": resnet32(), # this is the resnet-32x4
    "ResNet56": resnet56(),
    "ResNet110": resnet110()
}

# Path mapping for pretrained weights (adjust paths if needed)
weights_dict = {
    # "ResNet20": "/path/to/resnet20.pth",
    # "ResNet32": "/kaggle/input/resnet32/pytorch/default/1/ckpt_epoch_240.pth",
    "ResNet56":  "/kaggle/input/resnet-56/ckpt_epoch_240.pth",
    "ResNet110": "/kaggle/input/resnet-110/ckpt_epoch_240.pth"
}

# ---------------------------
# Evaluation loop
# ---------------------------
for name, constructor in model_dict.items():
    print(f"Evaluating {name}...")
    model = constructor.to(device)
    
    # Load pretrained weights if available
    weight_path = weights_dict.get(name)
    if weight_path:
        checkpoint = torch.load(weight_path, map_location=device,weights_only=False)
        if 'model' in checkpoint:
            state_dict = checkpoint['model']
        else:
            state_dict = checkpoint
        model.load_state_dict(state_dict)
    
    model.eval()
    correct = total = 0
    with torch.no_grad():
        for imgs, labels in test_loader:
            imgs, labels = imgs.to(device), labels.to(device)
            logits = model(imgs)
            preds = logits.argmax(1)
            correct += (preds == labels).sum().item()
            total += labels.size(0)

    test_acc = 100 * correct / total
    print(f"🎯 {name} Test Accuracy on CIFAR-100: {test_acc:.2f}%\n")


100%|██████████| 169M/169M [00:02<00:00, 58.3MB/s]


Evaluating ResNet56...
🎯 ResNet56 Test Accuracy on CIFAR-100: 72.41%

Evaluating ResNet110...
🎯 ResNet110 Test Accuracy on CIFAR-100: 74.31%



# Training the student models BASIC Resnet 20 / 32

import os
import math
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader, Subset
from torchvision import datasets, transforms
from torchvision.transforms import AutoAugment, AutoAugmentPolicy, RandomErasing
from tqdm.auto import tqdm
#from torchvision.models import resnet18, resnet34



device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
use_dp = torch.cuda.device_count() > 1
torch.manual_seed(42)
np.random.seed(42)

mean = (0.5071, 0.4867, 0.4408)  # CIFAR-100 mean
std  = (0.2675, 0.2565, 0.2761)  # CIFAR-100 std

batch_size = 64

# Precompute DataLoaders for each resolution
stages = [(r) for r in [(32, 240)]]
dataloader_dict = {}

'''
Copied from the paper as it is.

they are not using any validation sets. Training it on the entire train set!
    train_transform = transforms.Compose([
        transforms.RandomCrop(32, padding=4),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        transforms.Normalize(mean=mean, std=stdv),
    ])
    test_transform = transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize(mean=mean, std=stdv),
    ])
    
    '''

for resolution, _ in stages:
    train_tf = transforms.Compose([
        transforms.RandomCrop(resolution,padding=4),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        transforms.Normalize(mean, std),
    ])
    
    train_set = datasets.CIFAR100('./data', train=True, download=False, transform=train_tf)
    
    train_loader = DataLoader(train_set, batch_size=batch_size,
                              shuffle=True, num_workers=0, pin_memory=True)
    dataloader_dict[resolution] = {
        'train': train_loader
    }

# Test loader (fixed resolution)
test_tf = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize(mean, std),
])

test_ds = datasets.CIFAR100('./data', train=False, transform=test_tf)
test_loader = DataLoader(test_ds, batch_size=batch_size, shuffle=False, num_workers=0, pin_memory=True)


# learning_rate is divided by 10 

# ---------------------------
# Test loop
# ---------------------------

def test(Test_model):
    
    Test_model.eval()
    correct_val = total_val = 0
    
    with torch.no_grad():
        for imgs, labels in test_loader:
            imgs, labels = imgs.to(device), labels.to(device)
            logits = Test_model(imgs)
            preds = logits.argmax(1)
            correct_val += (preds == labels).sum().item()
            total_val += labels.size(0)
    test_acc = 100 * correct_val / total_val

    # print(f"Test Acc = {val_acc:.2f}%")
    return test_acc

# ---------------------------
# Training loop
# ---------------------------

def train(model, model_type):
    
    # Loss + optimizer
    lr = 0.05 # as per the paper
    criterion = nn.CrossEntropyLoss()
    optimizer = optim.SGD(model.parameters(), lr=lr, momentum=0.9, weight_decay=5e-4)

    # Step LR schedule: decay at 150, 180, 210 epochs
    scheduler = optim.lr_scheduler.MultiStepLR(optimizer, milestones=[150, 180, 210], gamma=0.1)

    best_val_acc = 0.0
    num_epochs = 240
    
    for res, epochs in stages:
        
        print(f"\n=== Training at resolution {res}px ===")
        tr_loader = dataloader_dict[res]['train']
        
        for e in range(1, epochs+1):
            
            model.train()
            total_loss = 0
            correct = total = 0
        
            for imgs, labels in tqdm(tr_loader, desc=f"Epoch {e}/{num_epochs}"):
                
                imgs, labels = imgs.to(device), labels.to(device)
                optimizer.zero_grad()
                logits = model(imgs)
                loss = criterion(logits, labels)
                loss.backward()
                optimizer.step()
        
                total_loss += loss.item()
                preds = logits.argmax(1)
                correct += (preds == labels).sum().item()
                total += labels.size(0)
        
            train_acc = 100 * correct / total
            scheduler.step()

            test_acc = test(model)
            
            print(f"Epoch {e}: Train Acc = {train_acc:.2f}% Test Accuracy = {test_acc:.2f}%") 
            
            # Save best model
            if test_acc > best_val_acc:
                best_val_acc = test_acc
                torch.save(model.state_dict(), f"resnet{model_type}_student.pth")
                print(f"→ Saved best model at epoch {e} with Test Acc = {train_acc:.2f}%")
    print("✅ Training completed!")

# KD Training Vanilla


In [3]:
import os
import math
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader, Subset
from torchvision import datasets, transforms
from torchvision.transforms import AutoAugment, AutoAugmentPolicy, RandomErasing
from tqdm.auto import tqdm
#from torchvision.models import resnet18, resnet34
from torchvision import datasets, transforms
from torch.utils.data import DataLoader


mean = (0.5071, 0.4867, 0.4408)
std  = (0.2675, 0.2565, 0.2761)
batch_size = 128
num_workers = 0
pin_mem = True

@torch.no_grad()
def evaluate(model, loader, device):
    model.eval()
    correct = total = 0
    for x, y in loader:
        x, y = x.to(device), y.to(device)
        logits = model(x)
        pred = logits.argmax(1)
        correct += (pred == y).sum().item()
        total += y.size(0)
    return 100.0 * correct / total


torch.manual_seed(27)
np.random.seed(27)

torch.cuda.manual_seed_all(27)
torch.backends.cudnn.deterministic = False
torch.backends.cudnn.benchmark = True



In [4]:
stages = [(r) for r in [(32, 240)]]
dataloader_dict = {}

# --- Build train loader(s) for each stage ---
for resolution, _ in stages:
    train_tf = transforms.Compose([
        transforms.RandomCrop(resolution, padding=4),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        transforms.Normalize(mean, std),
    ])

    train_set = datasets.CIFAR100('./data', train=True, download=True, transform=train_tf)
    train_loader = DataLoader(train_set, batch_size=batch_size, shuffle=True,
                              num_workers=num_workers, pin_memory=pin_mem)

    dataloader_dict[resolution] = {'train': train_loader}

# --- Single test loader (fixed 32x32 normalization) ---
test_tf = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize(mean, std),
])
test_set = datasets.CIFAR100('./data', train=False, download=True, transform=test_tf)
test_loader = DataLoader(test_set, batch_size=batch_size, shuffle=False,
                         num_workers=num_workers, pin_memory=pin_mem)

# --- Pick the 32px stage and call KD training ---
resolution, _ = stages[0]          # (32, 240)
train_loader = dataloader_dict[resolution]['train']


In [5]:
# learning_rate is divided by 10 
# ---------------------------
# Training loop
# ---------------------------

def kd_loss(student_logits, teacher_logits, labels, T=4.0, alpha=0.9): 
    """
    alpha = 0.1 as per the github repo
    Compute KD loss = α * KD + (1-α) * CE
    T = temperature
    α = weight for soft distillation loss
    """
    # Hard-label loss
    ce = F.cross_entropy(student_logits, labels)
    kd = F.kl_div(
        F.log_softmax(student_logits / T, dim=1),
        F.softmax(teacher_logits / T, dim=1),
        reduction="batchmean") * (T * T)
    
    return (1 - alpha) * ce + alpha * kd

In [6]:
def train_via_KD(t_model, s_model, train_loader, test_loader, device,
                 epochs=240, base_lr=0.05, wd=5e-4, milestones=(150,180,210),
                 T=4.0, alpha=0.9, save_path="student_kd.pth"):

    # Freeze teacher
    t_model.to(device).eval()
    for p in t_model.parameters():
        p.requires_grad = False

    s_model = s_model.to(device)

    optimizer = optim.SGD(s_model.parameters(), lr=base_lr, momentum=0.9, weight_decay=wd)
    scheduler = optim.lr_scheduler.MultiStepLR(optimizer, milestones=list(milestones), gamma=0.1)

    best_test = -1.0
    for e in range(1, epochs + 1):
        s_model.train()
        running_loss, correct, total = 0.0, 0, 0

        for imgs, labels in tqdm(train_loader, desc=f"Epoch {e}/{epochs}"):
            imgs, labels = imgs.to(device), labels.to(device)

            with torch.no_grad():
                t_logits = t_model(imgs)

            s_logits = s_model(imgs)
            loss = kd_loss(s_logits, t_logits, labels, T=T, alpha=alpha)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            running_loss += loss.item() * imgs.size(0)
            preds = s_logits.argmax(1)
            correct += (preds == labels).sum().item()
            total += labels.size(0)

        scheduler.step()
        train_loss = running_loss / total
        train_acc  = 100.0 * correct / total
        test_acc   = evaluate(s_model, test_loader, device)

        print(f"Epoch {e:3d}/{epochs} | loss {train_loss:.3f} | train {train_acc:5.2f}% | test {test_acc:5.2f}%")

        if test_acc > best_test:
            best_test = test_acc
            to_save = s_model.module.state_dict() if isinstance(s_model, torch.nn.DataParallel) else s_model.state_dict()
            torch.save(to_save, save_path)
            print(f"  ↳ Saved best @ epoch {e} (test {best_test:.2f}%) → {save_path}")

    print(f"✅ KD training finished. Best Test Acc: {best_test:.2f}%")


In [7]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
teacher = resnet56(num_classes = 100)
t_ckpt  = torch.load("/kaggle/input/resnet-56/ckpt_epoch_240.pth", map_location=device, weights_only=False)
teacher.load_state_dict(t_ckpt['model'] if 'model' in t_ckpt else t_ckpt)

student = resnet20(num_classes=100)

train_via_KD(teacher, student, train_loader, test_loader, device, save_path= "56_t-20_s.pth")

Epoch 1/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch   1/240 | loss 12.014 | train  9.05% | test 12.12%
  ↳ Saved best @ epoch 1 (test 12.12%) → 56_t-20_s.pth


Epoch 2/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch   2/240 | loss 9.440 | train 20.84% | test 21.26%
  ↳ Saved best @ epoch 2 (test 21.26%) → 56_t-20_s.pth


Epoch 3/240:   0%|          | 0/391 [00:00<?, ?it/s]

...

Epoch 238/240 | loss 1.694 | train 80.07% | test 70.78%


Epoch 239/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch 239/240 | loss 1.694 | train 80.13% | test 70.90%


Epoch 240/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch 240/240 | loss 1.689 | train 79.98% | test 70.95%
✅ KD training finished. Best Test Acc: 71.01%


In [8]:

teacher = resnet110(num_classes = 100)
t_ckpt  = torch.load("/kaggle/input/resnet-110/ckpt_epoch_240.pth", map_location=device, weights_only=False)
teacher.load_state_dict(t_ckpt['model'] if 'model' in t_ckpt else t_ckpt)

student = resnet20(num_classes=100)

train_via_KD(teacher, student, train_loader, test_loader, device, save_path= "110_t-20_s.pth")

Epoch 1/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch   1/240 | loss 14.768 | train  8.68% | test 13.79%
  ↳ Saved best @ epoch 1 (test 13.79%) → 110_t-20_s.pth


Epoch 2/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch   2/240 | loss 12.182 | train 19.06% | test 17.59%
  ↳ Saved best @ epoch 2 (test 17.59%) → 110_t-20_s.pth


Epoch 3/240:   0%|          | 0/391 [00:00<?, ?it/s]

...

Epoch 238/240 | loss 2.314 | train 81.01% | test 71.15%


Epoch 239/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch 239/240 | loss 2.309 | train 81.16% | test 71.20%


Epoch 240/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch 240/240 | loss 2.316 | train 80.94% | test 71.05%
✅ KD training finished. Best Test Acc: 71.23%


In [9]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
teacher = resnet110(num_classes = 100)
t_ckpt  = torch.load("/kaggle/input/resnet-110/ckpt_epoch_240.pth", map_location=device, weights_only=False)
teacher.load_state_dict(t_ckpt['model'] if 'model' in t_ckpt else t_ckpt)

student = resnet32_basic(num_classes=100)

train_via_KD(teacher, student, train_loader, test_loader, device, save_path= "110_t-32_s.pth")

Epoch 1/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch   1/240 | loss 14.864 | train  7.82% | test 12.00%
  ↳ Saved best @ epoch 1 (test 12.00%) → 110_t-32_s.pth


Epoch 2/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch   2/240 | loss 12.175 | train 18.45% | test 18.66%
  ↳ Saved best @ epoch 2 (test 18.66%) → 110_t-32_s.pth


Epoch 3/240:   0%|          | 0/391 [00:00<?, ?it/s]

...

Epoch 238/240 | loss 1.687 | train 86.93% | test 72.99%


Epoch 239/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch 239/240 | loss 1.680 | train 86.94% | test 73.13%


Epoch 240/240:   0%|          | 0/391 [00:00<?, ?it/s]

Epoch 240/240 | loss 1.682 | train 86.96% | test 73.16%
✅ KD training finished. Best Test Acc: 73.37%
